# Sentinel-3 L2 OLCI data handling and visualization

Let's monitor changes into OLCI variables of interest over a common geographical area. The datasets are extracted from S3 L2 OLCI _Land_ and _Water_ Full Resolution products using the `xarray` Python package, re-arranged and concatenated together into a final 3d data array which depth is the new _time_ dimension.

In [1]:
import os, sys
sys.path.append(os.path.join(os.path.expanduser("~"),"Trials/modules"))
import qm
import data_processing_S3_olci as dp
import hvplot.xarray

You can choose to work with local files or using the Advanced API. Functions in this tutorial can manage both choices independently and automatically, but only if product of interest are provided as an input list. <br>
### Using the Advanced API (ENS)
In this case your list must contain the position of products in the remote file system. Note that this list is automatically provided using the `SEARCH.ipynb` trial notebook, aimed at facilitating the data access via ENS. Products are found via ENS at their pseudopath, accessed and processed in situ, without any local download. <br>
### Using OData API
Alternatively you can load a custom list containing the products downloaded in the `local_files` folder. To do that, you can use the `download` function provided in the `qm` module, which will download and save items via your own Jupyter Notebook using OData protocol. Follow the example provided below or check out `DISCOVER_ONDA.ipynb`. <br>
👇 To download a product of interest run the cell below and find out the item in the 📁`local_files` folder placed in your root workspace. The 📄`list_local.txt` file will be created and updated in this working directory with the new downloaded item authomatically.

In [2]:
# define the input product list here
files = dp.products("list_WFR.txt")

👉 OLCI L2 variables are collected in the `switcher` dictionary variable from the `dp` module, but keys can be assigned depending on the OLCI product type itself, as shown in the table below:

| _LFR_ | _WFR_ |
| --- | --- |
| `OTCI` OLCI Terrestrial Clorophyll Index| `TSM_NN` Total suspended matter concentration (Neural Net)|
| `OGVI` OLCI Global Vegetation Index | `CHL_OC4ME` Algal pigment concentration|
| `IWV` Integrated water vapour column above the current pixel|`CHL_NN` Algal pigment concentration (Neural Net)|
||`IWV` Integrated water vapour column above the current pixel|

In [3]:
dp.switcher.keys()

dict_keys(['TSM_NN', 'CHL_OC4ME', 'CHL_NN', 'IWV', 'OTCI', 'OGVI'])

Here below the data set is created on the variable of interest given as input. Put `(xmin,xmax,ymin,ymax)` as the `bounds` argument of the function `make_ds` if you want to create a subsample.

In [4]:
v = "TSM_NN" # variable of interest here compliant to the product type (WFR or LFR)
ds = dp.make_ds(files,key=v)  

## Dynamical Map Visualisation

In this example we show two WFR products over Italy, the first sensed before the COVID-19 lockdown, the second one after a few weeks. Majour changes in the TSM are interesting the port areas (e.g. Genoa), rivers and their mouths (e.g. Po and Delta Po mouth) and lakes (e.g. Trasimeno).<br>
📌 We suggest to keep the `rainbow` colormap for OLCI water indexes, while specifying a `gist_earth_r` colormap for land items, for a better visualisation.

In [5]:
import cartopy.crs as ccrs
im_0 = ds.isel(time=0).hvplot.quadmesh(x='lon',y='lat',z=v,cmap="rainbow",clabel=ds[v].attrs["units"],
                                       title=str(ds.coords["time"].data[0]),
                                       rasterize=True,
                                       crs=ccrs.PlateCarree(),projection=ccrs.PlateCarree(),
                                       project=True,geo=True,coastline="50m")

im_1 = ds.isel(time=1).hvplot.quadmesh(x='lon',y='lat',z=v,cmap="rainbow",clabel=ds[v].attrs["units"],
                                       rasterize=True,title=str(ds.coords["time"].data[1]),
                                       crs=ccrs.PlateCarree(),projection=ccrs.PlateCarree(),
                                       project=True,geo=True,coastline="50m")
(im_0+im_1).cols(1)

:Layout
   .DynamicMap.I  :DynamicMap   []
      :Overlay
         .Image.I     :Image   [lon,lat]   (TSM_NN)
         .Coastline.I :Feature   [Longitude,Latitude]
   .DynamicMap.II :DynamicMap   []
      :Overlay
         .Image.I     :Image   [lon,lat]   (TSM_NN)
         .Coastline.I :Feature   [Longitude,Latitude]